# 모델링

In [1]:
# 필요 라이브러리 import
import numpy as np
import pandas as pd
from pyarrow import csv
import matplotlib.pyplot as plt
import seaborn as sns
import math

import tensorflow as tf
import cx_Oracle
from tensorflow import keras
from tensorflow.keras.layers import Dense,Flatten,Conv1D,Dropout,MaxPool1D,BatchNormalization,Dropout
from tensorflow.keras.models import Sequential ,Model
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.losses import mse,mae
from tensorflow.keras.callbacks import EarlyStopping,ModelCheckpoint
from tensorflow.keras import backend as K
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error ,mean_absolute_error,confusion_matrix ,r2_score

import os

In [2]:
CONN_INFO = {
        'NAME': 'XEPDB1',
        'USER': 'iitp',
        'PASSWORD': 'iitp',
        'HOST': '172.16.5.231',
        'PORT': '11521',
}
CONN_STR = '{USER}/{PASSWORD}@{HOST}:{PORT}/{NAME}'.format(**CONN_INFO)
conn = cx_Oracle.connect(CONN_STR)
cursor = conn.cursor()


def df_round(df , cols = ['이혼율','고용률','실업률','한국인_남녀비율','한국인_인구밀도','경찰청_인원_명당_담당_인구']):
    count_col_name= df.columns.to_list()
    for colN in cols:
        count_col_name.remove(colN)
    for colN in count_col_name:
        df[colN] = df[colN].round()
    df['시도'] = df['시도'].astype(int)
    df['년도'] = df['년도'].astype(int)
    return df

In [3]:
sido_code = pd.read_sql("select * from sido_code",con=conn) 
sido_code['CODE'] = sido_code['CODE'].astype(int)
sejong_code = sido_code[sido_code.KOR_NAME == '세종'].iloc[0]['CODE']

crime_code =  pd.read_sql("select * from crime_Specification",con=conn)
crime_code['CODE'] = crime_code['CODE'].astype(int)

indi_val = df_round(pd.read_sql("select * from independent_val",con=conn).astype(float) )
indi_val = indi_val[indi_val.시도 != sejong_code]

indi_zero = df_round(pd.read_sql("select * from independent_zero",con=conn).astype(float) )
indi_zero = indi_zero[indi_zero.시도 != sejong_code]

indi_mean = df_round(pd.read_sql("select * from independent_mean",con=conn).astype(float) )
indi_mean = indi_mean[indi_mean.시도 != sejong_code]

crime_val = pd.read_sql("select * from crime",con=conn).astype(float) 
crime_val['시도'] = crime_val['시도'].astype(int)
crime_val['년도'] = crime_val['년도'].astype(int)
crime_val = crime_val[crime_val.시도 != sejong_code]

1. 년도
    - crime_val : 2002~ 2019
    - indi_val  : 2000 ~ 2020  
    - indi_zero : 2002 ~ 2030
    - indi_mean : 2002 ~ 2030


In [4]:
# 모델생성

# 단순 Dense 모델
def create_Dense_model(x,y,loss_ = keras.losses.mse,optimizer_ = "adam"):
    model = Sequential([
        Dense(256, input_dim = x.shape[1], activation='relu', kernel_initializer='he_normal'),Dropout(0.5),
        Dense(256,activation = 'relu', kernel_initializer='he_normal'),Dropout(0.5),
        Dense(128,activation = 'relu', kernel_initializer='he_normal'),Dropout(0.3),
        Dense(128,activation = 'relu',kernel_initializer='he_normal'),Dropout(0.3),
        Dense(128, activation = 'relu', kernel_initializer='he_normal'),Dropout(0.3),
        Dense(64, activation = 'relu', kernel_initializer='he_normal'),Dropout(0.3),
        Dense(64, activation = 'relu', kernel_initializer='he_normal'),Dropout(0.3),
        Dense(64, activation = 'relu', kernel_initializer='he_normal'),Dropout(0.3),
        Dense(32, activation = 'relu', kernel_initializer='he_normal'),Dropout(0.3),
        Dense(16, activation = 'relu', kernel_initializer='he_normal'),
        Dense(1, activation = 'linear')    
    ])
    model.compile(
        loss = loss_, 
        optimizer = optimizer_,
        metrics = ['mae']
    )
    # model.summary()
    return model


# CNN Model 생성및 컴파일
# CNN Model 생성및 컴파일
def create_conv1d_model(x,y,loss_ = keras.losses.mse,optimizer_ = 'adam'):
    model = Sequential([        
        Conv1D(256, 2, padding='valid', activation='relu',input_shape = (x.shape[1],1),kernel_initializer='he_normal'),Dropout(0.5),
        MaxPool1D(), BatchNormalization(),
        Conv1D(256, 2, padding='same', activation='relu',kernel_initializer='he_normal'),Dropout(0.5),
        Conv1D(256, 2, padding='same', activation='relu',kernel_initializer='he_normal'),Dropout(0.5),
        Conv1D(256, 2, padding='same', activation='relu',kernel_initializer='he_normal'),Dropout(0.5),
        BatchNormalization(), 
        Conv1D(128, 2, padding='same', activation='relu',kernel_initializer='he_normal'),Dropout(0.5),
        Conv1D(128, 2, padding='same', activation='relu',kernel_initializer='he_normal'),Dropout(0.5),
        Conv1D(128, 2, padding='same', activation='relu',kernel_initializer='he_normal'),Dropout(0.5),
        MaxPool1D(), BatchNormalization(), 
        Flatten(),
        Dense(512,activation = 'relu', kernel_initializer='he_normal'),
        Dense(256,activation = 'relu', kernel_initializer='he_normal'),
        Dense(128,activation = 'relu', kernel_initializer='he_normal'),
        Dense(1,activation = 'linear')    
    ])
    model.compile( 
        loss = loss_,
        optimizer = optimizer_,
        metrics = ['mae']
    )
    # model.summary()
    return model


In [5]:
#훈련결과 확인 및 그래프 저장
def save_train_history(history,title):
    print(history.history.keys())

    img_path = '../img'
    path = img_path+'/train_history/'
    if not os.path.isdir(img_path):
        os.mkdir(img_path)
    if not os.path.isdir(path):
        os.mkdir(path)
    hist_dict = history.history
    loss = hist_dict['loss']
    val_loss = hist_dict['val_loss']
    acc = hist_dict['mae']
    val_acc = hist_dict['val_mae']
    
    plt.subplot(2,1,1)
    plt.title(title)
    plt.plot(loss, 'b--', label = 'train loss')
    plt.plot(val_loss, 'r:' , label = 'val loss')
    plt.legend()
    plt.grid()
        
    plt.subplot(2,1,2)
    plt.title(title)
    plt.plot(acc, 'b--', label = 'train mae')
    plt.plot(val_acc, 'r:' , label = 'val mae')
    plt.legend()
    plt.grid()
    
    plt.tight_layout()
    plt.savefig(path+title) 
    plt.clf()


# Dense모델 훈련 및 저장
def dense_fit(x_train,y_train,compare_,losses_,optimizers_,lName,oName):
    modelsPath = '../data/models/' 
    model_checkPoint = modelsPath + 'checkPoint/' 
    checkPoint_Name = f'{compare_}_Dense_{lName}_{oName}'
    if not os.path.isdir(model_checkPoint):
            os.mkdir(model_checkPoint)
    if not os.path.isdir(modelsPath + f'{compare_}'):
            os.mkdir(modelsPath + f'{compare_}')
    if not os.path.isdir(modelsPath + f'{compare_}/dense/'):
            os.mkdir(modelsPath + f'{compare_}/dense/')

    model = create_Dense_model(
        x = x_train,
        y = y_train,
        loss_ = losses_,
        optimizer_ = optimizers_
    ) 
    print(f'start {checkPoint_Name}')
    es = EarlyStopping(monitor='val_loss', mode='min', verbose=1,patience=1000) 
    mc = ModelCheckpoint(model_checkPoint+ checkPoint_Name+'.h5', monitor='val_mae', mode='min', save_best_only=True)
    with tf.device('/device:GPU:0'):
        history = model.fit(
            x = x_train,
            y = y_train,
            epochs= 50000, 
            batch_size= 1024,
            verbose= 1, # 훈련 횟수가 많아지면서, Ram점유율이 너무 높아져서 훈련과정 출력 안 게 설정
            callbacks=[es,mc],
            validation_split=0.2
        )

    model = create_Dense_model(
        x = x_train,
        y = y_train,
        loss_ = losses_,
        optimizer_ = optimizers_
    ) 
    # 저장된 가장 결과가 좋은 checkPoint 로드
    model.load_weights(model_checkPoint+ checkPoint_Name+'.h5') 
    # 모델 평가 
    loss,acc = model.evaluate(x_test,y_test, verbose=0) 
    # 모델 저장 
    model.save(modelsPath + f'{compare_}/dense/'+ checkPoint_Name+ f'_loss({loss:.2f})_mae({acc:.2f}).h5')
    save_train_history(
        history,
        title = checkPoint_Name+ f'_loss({loss:.2f})_mae({acc:5.2f}).png'
        )
    return history

# Dense모델 훈련 및 저장
def conv_fit(x_train,y_train,compare_,losses_,optimizers_,lName,oName):
    modelsPath = '../data/models/' 
    model_checkPoint = modelsPath + 'checkPoint/' 
    checkPoint_Name = f'{compare_}_conv_{lName}_{oName}'
    if not os.path.isdir(model_checkPoint):
            os.mkdir(model_checkPoint)
    if not os.path.isdir(modelsPath + f'{compare_}'):
            os.mkdir(modelsPath + f'{compare_}')
    if not os.path.isdir(modelsPath + f'{compare_}/conv/'):
            os.mkdir(modelsPath + f'{compare_}/conv/')
                
    model = create_conv1d_model(
        x = x_train,
        y = y_train,
        loss_ = losses_,
        optimizer_ = optimizers_
    )  

    es = EarlyStopping(monitor='val_loss', mode='min', verbose=1,patience=1000) # 시간이 부족하여 patience를 500 -> 50으로 축소
    mc = ModelCheckpoint(model_checkPoint+ checkPoint_Name+'.h5', monitor='val_mae', mode='min', save_best_only=True)
    with tf.device('/device:GPU:0'):
        history = model.fit(
            x = x_train, y = y_train,
            epochs= 50000, 
            batch_size= 1024,
            verbose= 1, # 훈련 횟수가 많아지면서, Ram점유율이 너무 높아져서 훈련과정 출력 안 게 설정
            callbacks=[es,mc],
            validation_split=0.2)
            
    model = create_conv1d_model(
        x = x_train,
        y = y_train,
        loss_ = losses_,
        optimizer_ = optimizers_) 
    # 저장된 가장 결과가 좋은 checkPoint 로드
    model.load_weights(model_checkPoint+ checkPoint_Name+'.h5') 
    # 모델 평가 
    loss,acc = model.evaluate(x_test,y_test, verbose=0) 

    # 모델 저장 
    model.save(modelsPath + f'{compare_}/conv/'+ checkPoint_Name+ f'_loss({loss:.2f})_mae({acc:.2f}).h5')
    save_train_history(
        history,
        title = checkPoint_Name+ f'_loss({loss:.2f})_mae({acc:5.2f}).png')
    return history

In [6]:

# for문을 이용하여 생각하는 loss함수 및 optimizer 모두 테스트 해보기위해 선언
# 모델 검증을 MAE로 하기 때문에 LOSS는 배제함
losses_ =[
    keras.losses.mse,
    # rmse,
    keras.losses.mae, 
    keras.losses.logcosh,
    ]
    
losses_name = [
    'mse',
    # 'rmse',
    'mae', 
    'logcosh'
]
# Adadelta는 다른 옵티마이저에비하여 성능은 부족하나, 사용하는 시간이 비정상정으로 높아서 배제함
optimizers_ = [
    keras.optimizers.Adam(learning_rate= 1e-5),
    keras.optimizers.RMSprop(learning_rate= 1e-5),
    keras.optimizers.SGD(learning_rate= 1e-5),
    keras.optimizers.Nadam(learning_rate= 1e-5),
    # keras.optimizers.Adadelta(learning_rate= 1e-5),
    # keras.optimizers.Adagrad(learning_rate= 1e-5),
    ]

optimizers_name = [
    'Adam',
    'RMSprop',
    'SGD',
    'Nadam',
    # 'Adadelta', 
    # 'Adagrad' 
]

def denseModelCheck(compare_):
    for loss_idx in range(len(losses_)):
        for optimizers_idx in range(len(optimizers_)) : 
            try:
                print(losses_name[loss_idx],optimizers_name[optimizers_idx])    
                history = dense_fit(
                    x_train = x_train,
                    y_train = y_train,
                    compare_ = compare_,
                    losses_ = losses_[loss_idx],
                    optimizers_ = optimizers_[optimizers_idx],
                    lName = losses_name[loss_idx],
                    oName=  optimizers_name[optimizers_idx]
                    )
            except:
                print(losses_name[loss_idx],optimizers_name[optimizers_idx],'Fail')
def conv1DModelCheck (compare_):
    for loss_idx in range(len(losses_)):
        for optimizers_idx in range(len(optimizers_)) : 
            try:
                history = conv_fit(
                    x_train = x_train,
                    y_train = y_train,
                    compare_ = compare_,
                    losses_ = losses_[loss_idx],
                    optimizers_ = optimizers_[optimizers_idx],
                    lName = losses_name[loss_idx],
                    oName=  optimizers_name[optimizers_idx]
                    )
            except:
                print(losses_name[loss_idx],optimizers_name[optimizers_idx],'Fail')    

In [7]:
import ast

colList = pd.read_sql("select * from topFiveCols",con=conn)

raw_x = indi_zero[(indi_zero.년도 <= 2019)].sort_values(['시도' ,'년도']).iloc[:,2:].reset_index(drop = True)

for crime_N in colList.CODE:
    x = raw_x[ast.literal_eval(colList.COLLIST[crime_N])]
    y = crime_val[crime_val.범죄종류 == crime_N].sort_values(['시도' ,'년도']).범죄수.reset_index(drop = True).fillna(0)
    # Conv1로 구성
    x_train, x_test,y_train, y_test = train_test_split(x,y,test_size=0.2)
    x_train = x_train.to_numpy().reshape(x_train.shape[0],x_train.shape[1],1)
    x_test = x_test.to_numpy().reshape(x_test.shape[0],x_test.shape[1],1)
    conv1DModelCheck(crime_code[crime_code.CODE == crime_N].CRIME_NAME.values[0]) 
    


Epoch 1/50000
1/1 [==============================] - 1s 1s/step - loss: 321519360.0000 - mae: 12175.3086 - val_loss: 345526304.0000 - val_mae: 13409.4238
Epoch 2/50000
1/1 [==============================] - 0s 26ms/step - loss: 321519200.0000 - mae: 12175.2334 - val_loss: 345538272.0000 - val_mae: 13409.6631
Epoch 3/50000
1/1 [==============================] - 0s 29ms/step - loss: 321513888.0000 - mae: 12175.1357 - val_loss: 345548448.0000 - val_mae: 13409.8779
Epoch 4/50000
1/1 [==============================] - 0s 27ms/step - loss: 321516352.0000 - mae: 12175.1816 - val_loss: 345552224.0000 - val_mae: 13409.9590
Epoch 5/50000
1/1 [==============================] - 0s 27ms/step - loss: 321513952.0000 - mae: 12175.1592 - val_loss: 345553952.0000 - val_mae: 13410.0039
Epoch 6/50000
1/1 [==============================] - 0s 22ms/step - loss: 321515392.0000 - mae: 12175.1387 - val_loss: 345555776.0000 - val_mae: 13410.0488
Epoch 7/50000
1/1 [==============================] - 0s 20ms/step 

C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\matplotlib\backends\backend_agg.py:240: RuntimeWarning: Glyph 51208 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\matplotlib\backends\backend_agg.py:240: RuntimeWarning: Glyph 46020 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\matplotlib\backends\backend_agg.py:203: RuntimeWarning: Glyph 51208 missing from current font.
  font.set_text(s, 0, flags=flags)
C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\matplotlib\backends\backend_agg.py:203: RuntimeWarning: Glyph 46020 missing from current font.
  font.set_text(s, 0, flags=flags)


Epoch 1/50000
1/1 [==============================] - 1s 923ms/step - loss: 321539904.0000 - mae: 12175.4141 - val_loss: 345457216.0000 - val_mae: 13408.0127
Epoch 2/50000
1/1 [==============================] - 0s 31ms/step - loss: 321533024.0000 - mae: 12175.2979 - val_loss: 345494560.0000 - val_mae: 13408.7686
Epoch 3/50000
1/1 [==============================] - 0s 16ms/step - loss: 321531648.0000 - mae: 12175.2559 - val_loss: 345509344.0000 - val_mae: 13409.0762
Epoch 4/50000
1/1 [==============================] - 0s 16ms/step - loss: 321528128.0000 - mae: 12175.1748 - val_loss: 345514880.0000 - val_mae: 13409.1982
Epoch 5/50000
1/1 [==============================] - 0s 16ms/step - loss: 321529120.0000 - mae: 12175.2012 - val_loss: 345521440.0000 - val_mae: 13409.3340
Epoch 6/50000
1/1 [==============================] - 0s 16ms/step - loss: 321521408.0000 - mae: 12175.0459 - val_loss: 345526304.0000 - val_mae: 13409.4375
Epoch 7/50000
1/1 [==============================] - 0s 31ms/st

C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\tensorflow\python\keras\callbacks.py:1664: RuntimeWarning: invalid value encountered in less
  if self.monitor_op(current - self.min_delta, self.best):
C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\tensorflow\python\keras\callbacks.py:1291: RuntimeWarning: invalid value encountered in less
  if self.monitor_op(current, self.best):


Epoch 12/50000
1/1 [==============================] - 0s 16ms/step - loss: nan - mae: nan - val_loss: nan - val_mae: nan
Epoch 13/50000
1/1 [==============================] - 0s 17ms/step - loss: nan - mae: nan - val_loss: nan - val_mae: nan
Epoch 14/50000
1/1 [==============================] - 0s 16ms/step - loss: nan - mae: nan - val_loss: nan - val_mae: nan
Epoch 15/50000
1/1 [==============================] - 0s 16ms/step - loss: nan - mae: nan - val_loss: nan - val_mae: nan
Epoch 16/50000
1/1 [==============================] - 0s 16ms/step - loss: nan - mae: nan - val_loss: nan - val_mae: nan
Epoch 17/50000
1/1 [==============================] - 0s 16ms/step - loss: nan - mae: nan - val_loss: nan - val_mae: nan
Epoch 18/50000
1/1 [==============================] - 0s 16ms/step - loss: nan - mae: nan - val_loss: nan - val_mae: nan
Epoch 19/50000
1/1 [==============================] - 0s 16ms/step - loss: nan - mae: nan - val_loss: nan - val_mae: nan
Epoch 20/50000
1/1 [============

In [7]:
import ast

colList = pd.read_sql("select * from topFiveCols",con=conn)

raw_x = indi_zero[(indi_zero.년도 <= 2019)].sort_values(['시도' ,'년도']).iloc[:,2:].reset_index(drop = True)
# raw_y = crime_val[crime_val.범죄종류 == 0].sort_values(['시도' ,'년도']).범죄수.reset_index(drop = True)
cnt= 0
for crime_N in colList.CODE:
    x = raw_x[ast.literal_eval(colList.COLLIST[crime_N])]
    y = crime_val[crime_val.범죄종류 == crime_N].sort_values(['시도' ,'년도']).범죄수.reset_index(drop = True).fillna(0)
    
    x_train, x_test,y_train, y_test = train_test_split(x,y,test_size=0.2)
    denseModelCheck(crime_code[crime_code.CODE == crime_N].CRIME_NAME.values[0])
    cnt+=1
cnt


mse Adam
start 절도_Dense_mse_Adam
Epoch 1/50000
1/1 [==============================] - 1s 610ms/step - loss: 24418554216448.0000 - mae: 2704300.2500 - val_loss: 557101875200.0000 - val_mae: 561260.2500
Epoch 2/50000
1/1 [==============================] - 3s 3s/step - loss: 51155790987264.0000 - mae: 3421615.2500 - val_loss: 556353060864.0000 - val_mae: 560905.1250
Epoch 3/50000
1/1 [==============================] - 0s 192ms/step - loss: 54649025462272.0000 - mae: 3193417.7500 - val_loss: 555877793792.0000 - val_mae: 560688.8750
Epoch 4/50000
1/1 [==============================] - 0s 347ms/step - loss: 47778180890624.0000 - mae: 3106761.0000 - val_loss: 554809556992.0000 - val_mae: 560162.8125
Epoch 5/50000
1/1 [==============================] - 0s 228ms/step - loss: 32865874083840.0000 - mae: 3094885.5000 - val_loss: 553282240512.0000 - val_mae: 559414.6875
Epoch 6/50000
1/1 [==============================] - 3s 3s/step - loss: 27433499623424.0000 - mae: 2841569.5000 - val_loss: 552097

C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\matplotlib\backends\backend_agg.py:240: RuntimeWarning: Glyph 51208 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\matplotlib\backends\backend_agg.py:240: RuntimeWarning: Glyph 46020 missing from current font.
  font.set_text(s, 0.0, flags=flags)
C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\matplotlib\backends\backend_agg.py:203: RuntimeWarning: Glyph 51208 missing from current font.
  font.set_text(s, 0, flags=flags)
C:\Users\painc\Anaconda3\envs\iitp_keras\lib\site-packages\matplotlib\backends\backend_agg.py:203: RuntimeWarning: Glyph 46020 missing from current font.
  font.set_text(s, 0, flags=flags)


mse RMSprop
start 절도_Dense_mse_RMSprop
Epoch 1/50000
1/1 [==============================] - 0s 420ms/step - loss: 34751528304640.0000 - mae: 3103536.0000 - val_loss: 777861595136.0000 - val_mae: 663074.6875
Epoch 2/50000
1/1 [==============================] - 0s 399ms/step - loss: 38591191318528.0000 - mae: 3286832.2500 - val_loss: 750126759936.0000 - val_mae: 651243.9375
Epoch 3/50000
1/1 [==============================] - 0s 252ms/step - loss: 29971332464640.0000 - mae: 3023793.5000 - val_loss: 729782484992.0000 - val_mae: 642247.6250
Epoch 4/50000
1/1 [==============================] - 0s 350ms/step - loss: 25569647394816.0000 - mae: 2963390.0000 - val_loss: 726401417216.0000 - val_mae: 640719.3750
Epoch 5/50000
1/1 [==============================] - 0s 338ms/step - loss: 37991657504768.0000 - mae: 3387587.5000 - val_loss: 713368403968.0000 - val_mae: 635439.1250
Epoch 6/50000
1/1 [==============================] - 0s 211ms/step - loss: 46432581058560.0000 - mae: 3330232.2500 - val_